## US dataset

* https://covidtracking.com/api
* https://www.census.gov/geographies/mapping-files/time-series/geo/carto-boundary-file.html

In [1]:
import pandas as pd
import numpy as np
import matplotlib as mpl
import pylab as plt
pd.set_option('display.width',140)
from bokeh.io import show, output_notebook
from bokeh.models import ColumnDataSource, GeoJSONDataSource, ColorBar, HoverTool, Legend, LogColorMapper, ColorBar
from bokeh.plotting import figure
from bokeh.palettes import brewer
from bokeh.layouts import row, column, gridplot
from bokeh.models import CustomJS, Select, MultiSelect, Plot, LinearAxis, Range1d, DatetimeTickFormatter
from bokeh.models.glyphs import Line, MultiLine
from bokeh.palettes import Category10
output_notebook()
#output_file('test.html')
import panel as pn
import panel.widgets as pnw
pn.extension()
import geopandas as gpd
import json

Loading BokehJS ...

In [2]:
daily = pd.read_csv('https://covidtracking.com/api/v1/states/daily.csv')
daily['date'] = pd.to_datetime(daily.date, format='%Y%m%d')

In [3]:
print (daily.columns)
daily[:4]

Index(['date', 'state', 'positive', 'negative', 'pending', 'hospitalizedCurrently', 'hospitalizedCumulative', 'inIcuCurrently',
       'inIcuCumulative', 'onVentilatorCurrently', 'onVentilatorCumulative', 'recovered', 'hash', 'dateChecked', 'death', 'hospitalized',
       'total', 'totalTestResults', 'posNeg', 'fips', 'deathIncrease', 'hospitalizedIncrease', 'negativeIncrease', 'positiveIncrease',
       'totalTestResultsIncrease'],
      dtype='object')


date state  positive  negative  pending  hospitalizedCurrently  hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
0 2020-04-04    AK     171.0    5869.0      NaN                    NaN                    16.0             NaN              NaN   
1 2020-04-04    AL    1580.0    9273.0      NaN                    NaN                   212.0             NaN              NaN   
2 2020-04-04    AR     743.0    9627.0      NaN                   72.0                     NaN             NaN              NaN   
3 2020-04-04    AS       NaN      20.0      6.0                    NaN                     NaN             NaN              NaN   

   onVentilatorCurrently  ...  hospitalized  total totalTestResults posNeg  fips  deathIncrease  hospitalizedIncrease  negativeIncrease  \
0                    NaN  ...          16.0   6040             6040   6040     2            2.0                   1.0              10.0   
1                    NaN  ...         212.0  10853            10853  10853     1            8.0                 212.0            1086.0   
2                   23.0  ...           NaN  10370            10370  10370     5            2.0                   0.0             632.0   
3                    NaN  ...           NaN     26               20     20    60            0.0                   0.0               0.0   

   positiveIncrease  totalTestResultsIncrease  
0              14.0                      24.0  
1             148.0                    1234.0  
2              39.0                     671.0  
3               0.0                       0.0  

[4 rows x 25 columns]

In [4]:
summary = daily.groupby('state')\
            .agg({'positive':np.sum,'hospitalized':np.sum,'negative':np.sum,'death':np.sum}).reset_index()

In [35]:
def get_geodata(shapefile):

    #Read shapefile using Geopandas
    gdf = gpd.read_file(shapefile)[['ADMIN', 'ADM0_A3', 'geometry']]
    #Rename columns.
    gdf.columns = ['country', 'country_code', 'geometry']
    gdf = gdf.drop(gdf.index[159])
    return gdf

def get_geodatasource(gdf):    
    """Get getjsondatasource from geopandas object"""
    json_data = json.dumps(json.loads(gdf.to_json()))
    return GeoJSONDataSource(geojson = json_data)

def bokeh_plot_map(gdf, column=None, title='', plot_width=950):
    """Plot bokeh map from GeoJSONDataSource """
    
    geosource = get_geodatasource(gdf)
    palette = brewer['Reds'][8]
    palette = palette[::-1]
    vals = gdf[column]
    columns = ['NAME','STUSPS','positive','negative','hospitalized','death']
    x = [(i, "@%s" %i) for i in columns]    
    hover = HoverTool(
        tooltips=x, point_policy='follow_mouse')
    color_mapper = LogColorMapper(palette = palette, low = vals.min(), high = vals.max())
    tools = ['wheel_zoom,pan,reset',hover]
    h = int(plot_width/2)
    p = figure(title = title, plot_height=h , plot_width=plot_width, toolbar_location='right', tools=tools)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    #Add patch renderer to figure
    p.patches('xs','ys', source=geosource, fill_alpha=1, line_width=0.5, line_color='black',  
              fill_color={'field' :column , 'transform': color_mapper})
    p.background_fill_color = "#e1e1ea"
    p.sizing_mode = 'scale_height'
    p.toolbar.logo = None
    return p

In [36]:
gdf = gpd.read_file('map_data/cb_2018_us_state_5m.shp')
gdf = gdf.merge(summary, left_on='STUSPS', right_on='state', how='inner')
gdf = gdf[~gdf.STUSPS.isin(['MP','GU','AS','PR','AK','HI','VI'])]
mp = bokeh_plot_map(gdf, 'positive', plot_width=600)

In [37]:
gdf[:2]

STATEFP   STATENS     AFFGEOID GEOID STUSPS        NAME LSAD         ALAND       AWATER  \
0      31  01779792  0400000US31    31     NE    Nebraska   00  198956658395   1371829134   
1      53  01779804  0400000US53    53     WA  Washington   00  172112588220  12559278850   

                                            geometry state  positive  hospitalized  negative   death  
0  POLYGON ((-104.05351 41.15726, -104.05267 41.2...    NE    2173.0           0.0   34657.0    30.0  
1  MULTIPOLYGON (((-122.32834 48.02134, -122.3217...    WA   66993.0        1778.0  812813.0  3113.0

In [38]:
pn.pane.Bokeh(mp)

Bokeh(Figure)

In [40]:
def plot_states(event):
    
    selection = state_select.value[:10]
    scale = scale_select.value
    column = col_select.value
    df = daily[daily.state.isin(selection)]
    colors = Category10[10] + Category10[10]    
    p = figure(plot_width=600,plot_height=400,x_axis_type='datetime',y_axis_type=scale,
               tools=[],title='Daily Data Per State',)
    i=0 
    for c,g in df.groupby('state'):    
        p.line(x=g.date, y=g[column], line_color=colors[i],line_width=3,line_alpha=.8,legend_label=c)     
        i+=1  
   
    p.yaxis.axis_label = column
    p.background_fill_color = "whitesmoke"
    p.background_fill_alpha = 0.5
    p.legend.location = "top_left"
    p.xaxis.axis_label = 'Date'
    p.xaxis.formatter=DatetimeTickFormatter(days="%d/%m",months="%m/%d %H:%M")
    p.toolbar.logo = None
    p.sizing_mode = 'scale_width'
    plot_pane.object = p
    return 


In [50]:
names = list(daily.state)
columns = list(daily.columns[2:])
state_select = pnw.MultiSelect(name="State", value=['NY','CA','FL','MI'], options=names, width=160)
state_select.param.watch(plot_states, 'value')
scale_select = pnw.Select(name="Scale", value='log', options=['linear','log'], width=160)
scale_select.param.watch(plot_states, 'value')
col_select = pnw.Select(name="Column", value='positive', options=columns, width=160)
col_select.param.watch(plot_states, 'value')

plot_pane = pn.pane.Bokeh()
plot = plot_states(None)
map_pane = pn.pane.Bokeh(mp,sizing_mode='stretch_both')

title=pn.pane.HTML('<h2>The COVID Tracking Project US dataset. <a>https://covidtracking.com/</a></h2>')
info=pn.pane.HTML('<p style="font-family: monospace;">The COVID Tracking Project is a curated dataset of daily cases. All information comes from state/district/territory public health authorities. It is updated each day between 4pm and 5pm EDT</p>')
app = pn.Column(title,pn.Row(pn.Column(state_select,scale_select,col_select),plot_pane,map_pane),info,sizing_mode='stretch_width')
app

Column(sizing_mode='stretch_width')
    [0] HTML(str)
    [1] Row
        [0] Column
            [0] MultiSelect(name='State', options=['AK', 'AL', 'AR', ...], value=['NY', 'CA', 'FL', 'MI'], width=160)
            [1] Select(name='Scale', options=['linear', 'log'], value='log', width=160)
            [2] Select(name='Column', options=['positive', 'negative', ...], value='positive', width=160)
        [1] Bokeh(Figure)
        [2] Bokeh(Figure, sizing_mode='stretch_both')
    [2] HTML(str)

In [ ]:
app.servable(title='COVIDTracking dataset')